# 0. Importing Necessary Packages

In [1]:
# Printing the information of Python, IPython, OS, and the generation date.
%load_ext version_information
%version_information

Software versions
Python 2.7.17 64bit [GCC 7.3.0]
IPython 5.8.0
OS Linux 5.8.18 100.fc31.x86_64 x86_64 with fedora 31 Thirty_One
Sun Apr 10 00:21:20 2022 KST

In [2]:
# Printing the versions of packages
from importlib_metadata import version
for pkg in ['numpy', 'matplotlib', 'pandas', 'astropy', 'pyraf']:
    print(pkg+": ver "+version(pkg))

numpy: ver 1.16.5
matplotlib: ver 2.2.3
pandas: ver 0.24.2
astropy: ver 2.0.16
pyraf: ver 2.1.15


In [3]:
# matplotlib backend
%matplotlib notebook

# importing necessary modules
import time
import numpy as np
import glob, os
from matplotlib import pyplot as plt
import pandas as pd
from astropy.io import fits
from astropy.stats import sigma_clipped_stats
import astropy.units as u
from astropy.coordinates import SkyCoord
from astropy.coordinates import CartesianRepresentation
from astropy.coordinates import matching

current_dir = os.getcwd()
dir_iraf = os.path.abspath('../')    # where 'login.cl' file is located

os.chdir(dir_iraf)
from pyraf import iraf
os.chdir(current_dir)

# 1. Selecting PSF Stars in the Images

In [4]:
dir_img = "HolmIX/"
imglist = [dir_img+"HolmIX_g.fits", dir_img+"HolmIX_i.fits"]
n_img = len(imglist)
band = ["g", "i"]
imglist

['HolmIX/HolmIX_g.fits', 'HolmIX/HolmIX_i.fits']

In [5]:
# You can also run this command in terminal.
ds9_options = "-scalemode zscale -scale lock yes -frame lock image "
names = ""
for i in np.arange(n_img):
    names += imglist[i]+" "
ds9_command = "ds9 "+ds9_options+names+"&"
print('Running "'+ds9_command+'" in the terminal...')
os.system(ds9_command)

Running "ds9 -scalemode zscale -scale lock yes -frame lock image HolmIX/HolmIX_g.fits HolmIX/HolmIX_i.fits &" in the terminal...


0

In [6]:
p0_x, p0_y = np.loadtxt(dir_img+"init_point.reg").T

In [8]:
for i in np.arange(n_img):
    iraf.txdump("HolmIX/HolmIX_"+band[i]+".mag", "ID,XCENTER,YCENTER,MAG,MSKY", "yes",
                Stdout="HolmIX/tmp")
    dat_phot = np.genfromtxt("HolmIX/tmp", dtype='float', encoding="ascii",
                             names=("ID","XCENTER","YCENTER","MAG","MSKY"))
    
    coord_regr = SkyCoord(p0_x*u.m, p0_y*u.m, 0.*u.m,
                          representation='cartesian') # python 3 representation_type
    coord_phot = SkyCoord(dat_phot['XCENTER']*u.m, dat_phot['YCENTER']*u.m, 0.*u.m,
                          representation='cartesian')
    idx, sep2d, dist3d = matching.match_coordinates_sky(coord_regr, coord_phot)
    
    f = open(dir_img+"HolmIX_"+band[i]+".pst.0", "w")
    f.write("#N ID    XCENTER   YCENTER   MAG         MSKY \n")
    f.write("#U ##    pixels    pixels    magnitudes  counts \n")
    f.write("#F %-9d  %-10.3f   %-10.3f   %-12.3f     %-15.7g\n")
    f.write("#\n")
    for j in idx:
        f.write("{0:<9d} {1:<10.3f} {2:<10.3f} {3:<12.3f} {4:<15.7g}\n".format(int(dat_phot['ID'][j]),
                                                                     dat_phot['XCENTER'][j],
                                                                     dat_phot['YCENTER'][j],
                                                                     dat_phot['MAG'][j],
                                                                     dat_phot['MSKY'][j]))
    f.close()

In [9]:
iraf.noao()
iraf.digiphot()
iraf.daophot()

In [10]:
# img_g, hdr_g = fits.getdata(imglist[0], header=True)
# img_i, hdr_i = fits.getdata(imglist[1], header=True)

In [16]:
med_fwhm_g, med_fwhm_i = np.loadtxt(dir_img+"fwhms.txt").T
print(med_fwhm_g, med_fwhm_i)
fwhms = [med_fwhm_g, med_fwhm_i]

sky_value, sky_sigma = np.loadtxt(dir_img+"sky.txt")
print(sky_value, sky_sigma)

(3.845, 3.85)
(array([0.006295, 0.01383 ]), array([0.03368, 0.07592]))


# 2. Making a PSF Image

In [28]:
# PSF task (non-interative)
# If you want to do this interatively, please set "interactive" = True.
# (But the interactive PSF task could be a very annoying to you :>)

start_time = time.time()

for i in np.arange(n_img):
    print("\n----- Starting PSF task for "+imglist[i]+" -----\n")
    imgname = imglist[i].split(".fits")[0]
    magfile = imgname+".mag"
    kwargs = {"fwhmpsf":fwhms[i], "sigma":sky_sigma[i],
              "datamax":100.0, "readnoi":5.0, "epadu":3.0, "itime":1.0,
              "psfrad":4.0*fwhms[i], "fitrad":1.0*fwhms[i]}
    
    n_iter = 1
    while True:
        psffile = imgname+".psf."+str(n_iter)+".fits"
        seepsffile = imgname+".spsf."+str(n_iter)+".fits"
        pstfile = imgname+".pst."+str(n_iter)
        psgfile = imgname+".psg."+str(n_iter)
        os.system("rm -rfv "+psffile+" "+seepsffile+" "+pstfile+" "+psgfile)
    
        iraf.psf(image=imglist[i], photfile=magfile, pstfile=imgname+".pst."+str(n_iter-1),
                 psfimage=psffile, opstfile=pstfile, groupfile=psgfile, 
                 function="auto", varorder=0, interactive=False, **kwargs)
        
        iraf.seepsf(psffile, seepsffile)
        ds9_command = "ds9 -scalemode zscale "+seepsffile+" &"
        os.system(ds9_command)

        response = raw_input("Are you satisfied? (Y/N)")
        if (response == "Y"):
            break
        elif (response == "N"):
            alsfile = imgname+".als."+str(n_iter)
            rejfile = imgname+".arj."+str(n_iter)
            subimage = imgname+".sub."+str(n_iter)+".fits"
            os.system("rm -rfv "+alsfile+" "+rejfile+" "+subimage)
            iraf.allstar(image=imglist[i], photfile=psgfile, psfimage=psffile,
                         allstarfile=alsfile, rejfile=rejfile, subimage=subimage, **kwargs)
            
            os.system("rm -rfv "+subimage)
            iraf.substar(image=imglist[i], photfile=alsfile, exfile=pstfile, psfimage=psffile,
                         subimage=subimage, **kwargs)
            
            ds9_command = "ds9 -scalemode zscale -scale lock yes -frame lock image "+ \
                          imglist[i]+" "+subimage+" &"
            os.system(ds9_command)
            
            n_iter += 1
        else:
            raise TypeError
            break
    
end_time = time.time()
print("\n--- PSF tasks take {0:.4f} sec ---".format(end_time-start_time))


----- Starting PSF task for HolmIX/HolmIX_g.fits -----


Analytic psf function(s) (auto): 	Analytic psf function(s): auto
Order of variable psf (0): 	Order of variable psf: 0
Psf radius in scale units (15.38): 	New psf radius: 15.38 scale units 15.38 pixels
Fitting radius in scale units (3.845): 	New fitting radius: 3.845 scale units 3.845 pixels
Minimum good data value (INDEF) (CR or value): 	New minimum good data value: INDEF counts
Maximum good data value (100.) (CR or value): 	New maximum good data value: 100. counts


Computing PSF for image: HolmIX/HolmIX_g.fits
5345 stars read from HolmIX/HolmIX_g.mag

Star 5268 has been added to the PSF star list
	X:  135.46 Y: 2148.27  Mag:  21.601  Dmin: -0.06291332  Dmax: 8.161823
Star 4924 has been added to the PSF star list
	X:   43.97 Y: 1644.06  Mag:  21.062  Dmin: -0.04324778  Dmax: 14.36388
Star 4955 has been added to the PSF star list
	X:  255.04 Y: 1691.58  Mag:  21.390  Dmin: -0.0726084  Dmax: 10.52991
Star 4984 has been added to t

REJECTING   - Star:   24 X =  813.38 Y =   57.40 Mag =   INDEF
REJECTING   - Star:  178 X = 1215.83 Y =  271.25 Mag =   INDEF
SUBTRACTING - Star:  183 X = 1201.15 Y =  277.91 Mag =   25.55
REJECTING   - Star:  257 X = 1941.24 Y =  407.77 Mag =   INDEF
REJECTING   - Star:  384 X = 1229.23 Y =  526.70 Mag =   INDEF
REJECTING   - Star:  459 X =  114.15 Y =  565.47 Mag =   INDEF
REJECTING   - Star:  669 X = 2232.68 Y =  648.06 Mag =   INDEF
SUBTRACTING - Star:  755 X = 2218.66 Y =  667.64 Mag =   25.51
SUBTRACTING - Star: 1955 X = 1401.73 Y =  902.00 Mag =   25.71
SUBTRACTING - Star: 1986 X = 1408.64 Y =  906.33 Mag =   25.27
SUBTRACTING - Star: 1985 X = 1398.88 Y =  906.43 Mag =   24.61
SUBTRACTING - Star: 2007 X = 1402.37 Y =  910.03 Mag =   24.06
SUBTRACTING - Star: 2016 X = 1396.72 Y =  911.15 Mag =   24.09
SUBTRACTING - Star: 2048 X = 1376.81 Y =  915.11 Mag =   24.86
SUBTRACTING - Star: 2059 X = 1410.66 Y =  917.80 Mag =   23.67
SUBTRACTING - Star: 2079 X = 1388.15 Y =  920.54 Mag = 

FITTING:   ID:  4924  XCEN:    43.99  YCEN:  1644.05  MAG:    21.05
FITTING:   ID:  4955  XCEN:   255.03  YCEN:  1691.59  MAG:    21.38
FITTING:   ID:  4984  XCEN:   505.04  YCEN:  1740.85  MAG:    21.99
FITTING:   ID:  5268  XCEN:   135.44  YCEN:  2148.28  MAG:    21.60
FITTING:   ID:  5325  XCEN:  1300.11  YCEN:  2240.41  MAG:    22.50
NITER = 5
FITTING:   ID:  2059  XCEN:  1410.66  YCEN:   917.80  MAG:    23.67
FITTING:   ID:  2118  XCEN:  1371.05  YCEN:   928.58  MAG:    25.02
FITTING:   ID:  2131  XCEN:  1395.42  YCEN:   929.23  MAG:    25.18
FITTING:   ID:  2235  XCEN:  1386.32  YCEN:   945.97  MAG:    22.66
FITTING:   ID:  3975  XCEN:  1307.74  YCEN:  1227.04  MAG:    25.01
FITTING:   ID:  4007  XCEN:  1284.65  YCEN:  1236.14  MAG:    24.78
FITTING:   ID:  4023  XCEN:  1288.14  YCEN:  1239.21  MAG:    25.58
FITTING:   ID:  4013  XCEN:  1307.11  YCEN:  1237.24  MAG:    25.25
NITER = 6
FITTING:   ID:  1986  XCEN:  1408.64  YCEN:   906.33  MAG:    25.27
FITTING:   ID:  3933  XCEN: 

	X: 1300.10 Y: 2240.48  Mag:  22.497  Dmin: -0.05751233  Dmax: 3.519091

15 PSF stars read from HolmIX/HolmIX_g.pst.2

Trying function gauss norm scatter = 0.06368815
Trying function lorentz norm scatter = 0.05874378
Trying function moffat15 norm scatter = 0.05489674
Trying function moffat25 norm scatter = 0.05488453
Trying function penny1 norm scatter = 0.05605851
Trying function penny2 norm scatter = 0.0561594
Best fitting function is moffat25

Analytic PSF fit 
    Function: moffat25  X: 1249.5  Y: 1149.5  Height: 19.96532  Psfmag: 21.601
    Par1: 1.780963  Par2: 1.818608  XYterm: -0.05748107  Moffat: 2.5

Computed 1 lookup table(s)

Writing PSF image HolmIX/HolmIX_g.psf.3.fits
Writing output PSF star list HolmIX/HolmIX_g.pst.3
Writing output PSF star group file HolmIX/HolmIX_g.psg.3
Are you satisfied? (Y/N)Y

----- Starting PSF task for HolmIX/HolmIX_i.fits -----


Analytic psf function(s) (auto): 	Analytic psf function(s): auto
Order of variable psf (0): 	Order of variable psf: 0

EXCLUDING   - Star:   24 X =  813.42 Y =   57.43 Mag =   INDEF
EXCLUDING   - Star:  178 X = 1215.86 Y =  271.27 Mag =   INDEF
EXCLUDING   - Star:  384 X = 1229.30 Y =  526.73 Mag =   INDEF
EXCLUDING   - Star:  257 X = 1941.26 Y =  407.78 Mag =   INDEF
EXCLUDING   - Star: 2131 X = 1395.34 Y =  929.28 Mag =   INDEF
EXCLUDING   - Star: 4028 X = 1302.21 Y = 1240.06 Mag =   INDEF
EXCLUDING   - Star: 5325 X = 1300.21 Y = 2240.42 Mag =   INDEF
REJECTING   - Star:   24 X =  813.42 Y =   57.43 Mag =   INDEF
REJECTING   - Star:  178 X = 1215.86 Y =  271.27 Mag =   INDEF
SUBTRACTING - Star:  183 X = 1200.90 Y =  277.84 Mag =   25.01
REJECTING   - Star:  257 X = 1941.26 Y =  407.78 Mag =   INDEF
REJECTING   - Star:  384 X = 1229.30 Y =  526.73 Mag =   INDEF
REJECTING   - Star:  459 X =  114.18 Y =  565.46 Mag =   INDEF
SUBTRACTING - Star: 1955 X = 1405.62 Y =  903.53 Mag =   24.74
SUBTRACTING - Star: 1985 X = 1398.73 Y =  906.67 Mag =   23.09
SUBTRACTING - Star: 1986 X = 1414.71 Y =  908.11 Mag = 

# 3. Photometry Using the PSF Model Image

In [50]:
# ALLSTAR task
start_time = time.time()

for i in np.arange(n_img):
    print("\n----- Starting ALLSTAR task for "+imglist[i]+" -----\n")
    imgname = imglist[i].split(".fits")[0]
    magfile = imgname+".mag"
    psffile = sorted(glob.glob(imgname+".psf.*.fits"))[-1]
    
    kwargs = {"fwhmpsf":fwhms[i], "sigma":sky_sigma[i],
              "datamax":100.0, "readnoi":5.0, "epadu":3.0, "itime":1.0,
              "psfrad":4.0*fwhms[i], "fitrad":1.0*fwhms[i]}

    alsfile = imgname+".als.A"
    rejfile = imgname+".arj.A"
    subimage = imgname+".sub.A.fits"
    os.system("rm -rfv "+alsfile+" "+rejfile+" "+subimage)
    
    iraf.allstar(image=imglist[i], photfile=magfile, psfimage=psffile,
                 allstarfile=alsfile, rejfile=rejfile, subimage=subimage, **kwargs)

    ds9_command = "ds9 -scalemode zscale -scale lock yes -frame lock image "+ \
                  imglist[i]+" "+subimage+" &"
    os.system(ds9_command)
    
end_time = time.time()
print("\n--- ALLSTAR tasks take {0:.4f} sec ---".format(end_time-start_time))


----- Starting ALLSTAR task for HolmIX/HolmIX_g.fits -----


Recenter the stars (yes): 	Recenter the stars: yes
Use group sky values (yes): 	Use group sky values: yes
Refit the sky (no): 	Refit the sky: no
Psf radius in scale units (15.38): 	New psf radius: 15.38 scale units 15.38 pixels
Fitting radius in scale units (3.845): 	New fitting radius: 3.845 scale units 3.845 pixels
Maximum group size in number of stars (60): 	New maximum group size: 60 stars
Minimum good data value (INDEF) (CR or value): 	New minimum good data value: INDEF counts
Maximum good data value (100.) (CR or value): 	New maximum good data value: 100. counts

REJECTING: Star 2237 has merged with star 2265
REJECTING: Star 2960 has merged with star 2967
NITER = 1
REJECTING: Star ID: 485 has too few good pixels
REJECTING: Star ID: 3922 has too few good pixels
REJECTING: Star ID: 4311 has too few good pixels
NITER = 2
NITER = 3
REJECTING: Star ID: 484 has too few good pixels
NITER = 4
FITTING:   ID:     4  XCEN:  1796.

FITTING:   ID:   169  XCEN:  1029.61  YCEN:   259.46  MAG:    26.05
FITTING:   ID:   170  XCEN:   758.47  YCEN:   262.02  MAG:    23.77
FITTING:   ID:   171  XCEN:  2252.97  YCEN:   262.95  MAG:    24.63
FITTING:   ID:   172  XCEN:   429.57  YCEN:   264.21  MAG:    24.57
FITTING:   ID:   173  XCEN:   134.25  YCEN:   265.97  MAG:    24.16
FITTING:   ID:   175  XCEN:  2353.49  YCEN:   267.61  MAG:    25.11
FITTING:   ID:   177  XCEN:   759.85  YCEN:   269.67  MAG:    25.03
FITTING:   ID:   178  XCEN:  1215.83  YCEN:   271.25  MAG:    22.29
FITTING:   ID:   179  XCEN:   978.73  YCEN:   275.90  MAG:    25.75
FITTING:   ID:   180  XCEN:  1095.73  YCEN:   276.60  MAG:    26.18
FITTING:   ID:   181  XCEN:   843.76  YCEN:   276.75  MAG:    25.68
FITTING:   ID:   183  XCEN:  1201.15  YCEN:   277.91  MAG:    25.55
FITTING:   ID:   182  XCEN:     6.52  YCEN:   278.42  MAG:    24.37
FITTING:   ID:   184  XCEN:   196.54  YCEN:   278.59  MAG:    25.03
FITTING:   ID:   185  XCEN:   913.59  YCEN:   28

FITTING:   ID:   355  XCEN:   922.94  YCEN:   508.18  MAG:    25.11
FITTING:   ID:   356  XCEN:  1275.10  YCEN:   508.25  MAG:    25.40
FITTING:   ID:   357  XCEN:   631.34  YCEN:   508.54  MAG:    25.37
FITTING:   ID:   358  XCEN:  2173.17  YCEN:   509.04  MAG:    24.83
FITTING:   ID:   359  XCEN:  1293.76  YCEN:   509.74  MAG:    25.59
FITTING:   ID:   361  XCEN:   324.83  YCEN:   511.69  MAG:    25.79
FITTING:   ID:   363  XCEN:  1735.45  YCEN:   511.93  MAG:    23.85
FITTING:   ID:   373  XCEN:  1732.62  YCEN:   518.27  MAG:    24.92
FITTING:   ID:   371  XCEN:  1648.07  YCEN:   516.77  MAG:    22.12
FITTING:   ID:   362  XCEN:   800.17  YCEN:   512.54  MAG:    24.62
FITTING:   ID:   368  XCEN:   211.11  YCEN:   515.91  MAG:    25.06
FITTING:   ID:   372  XCEN:  1076.49  YCEN:   517.79  MAG:    24.13
FITTING:   ID:   377  XCEN:  2379.11  YCEN:   521.69  MAG:    25.17
FITTING:   ID:   380  XCEN:  1312.75  YCEN:   522.39  MAG:    24.41
FITTING:   ID:   378  XCEN:   657.99  YCEN:   52

FITTING:   ID:   539  XCEN:   986.53  YCEN:   603.40  MAG:    26.43
FITTING:   ID:   543  XCEN:  1890.62  YCEN:   603.48  MAG:    25.73
FITTING:   ID:   598  XCEN:  1992.87  YCEN:   627.32  MAG:    21.21
FITTING:   ID:   551  XCEN:  2058.04  YCEN:   606.57  MAG:    24.90
FITTING:   ID:   552  XCEN:  2167.98  YCEN:   607.45  MAG:    25.72
FITTING:   ID:   557  XCEN:  1561.25  YCEN:   609.00  MAG:    24.14
FITTING:   ID:   555  XCEN:  1167.24  YCEN:   609.29  MAG:    25.90
FITTING:   ID:   558  XCEN:     5.12  YCEN:   609.73  MAG:    24.99
FITTING:   ID:   563  XCEN:  2316.73  YCEN:   610.07  MAG:    22.56
FITTING:   ID:   559  XCEN:  1600.59  YCEN:   610.36  MAG:    25.15
FITTING:   ID:   560  XCEN:  1651.15  YCEN:   610.36  MAG:    24.16
FITTING:   ID:   565  XCEN:  2013.60  YCEN:   610.98  MAG:    24.79
FITTING:   ID:   564  XCEN:  1291.26  YCEN:   611.28  MAG:    25.91
FITTING:   ID:   571  XCEN:  1675.79  YCEN:   616.44  MAG:    23.60
FITTING:   ID:   570  XCEN:  1644.03  YCEN:   61

FITTING:   ID:   736  XCEN:  2202.83  YCEN:   664.89  MAG:    25.72
FITTING:   ID:   737  XCEN:  1005.83  YCEN:   665.01  MAG:    25.44
FITTING:   ID:   738  XCEN:  1702.66  YCEN:   665.14  MAG:    24.78
FITTING:   ID:   742  XCEN:  2139.86  YCEN:   665.81  MAG:    24.09
FITTING:   ID:   741  XCEN:  2001.14  YCEN:   666.16  MAG:    23.05
FITTING:   ID:   739  XCEN:   882.35  YCEN:   666.54  MAG:    25.41
FITTING:   ID:   748  XCEN:  1949.07  YCEN:   666.60  MAG:    23.41
FITTING:   ID:   740  XCEN:  1653.66  YCEN:   666.82  MAG:    25.67
FITTING:   ID:   744  XCEN:  1554.91  YCEN:   667.13  MAG:    24.09
FITTING:   ID:   755  XCEN:  2218.66  YCEN:   667.64  MAG:    25.51
FITTING:   ID:   754  XCEN:  1983.36  YCEN:   667.79  MAG:    23.63
FITTING:   ID:   752  XCEN:  1902.97  YCEN:   667.92  MAG:    24.73
FITTING:   ID:   750  XCEN:  1255.01  YCEN:   668.02  MAG:    25.22
FITTING:   ID:   775  XCEN:  1254.74  YCEN:   674.22  MAG:    25.27
FITTING:   ID:   756  XCEN:  1077.34  YCEN:   66

...

FITTING:   ID:  3066  XCEN:  2470.44  YCEN:  1066.58  MAG:    25.20
FITTING:   ID:  3115  XCEN:  1155.12  YCEN:  1076.26  MAG:    24.88
FITTING:   ID:  3231  XCEN:  1375.06  YCEN:  1089.46  MAG:    24.28
FITTING:   ID:  3217  XCEN:  1123.36  YCEN:  1091.57  MAG:    24.63
REJECTING: Star ID: 3262 is too faint
FITTING:   ID:  3308  XCEN:  1585.26  YCEN:  1105.07  MAG:    22.33
FITTING:   ID:  3331  XCEN:  1529.92  YCEN:  1106.25  MAG:    25.67
FITTING:   ID:  3525  XCEN:  1593.09  YCEN:  1136.92  MAG:    25.75
FITTING:   ID:  3575  XCEN:   814.43  YCEN:  1146.38  MAG:    24.84
FITTING:   ID:  3602  XCEN:  1551.24  YCEN:  1149.48  MAG:    23.29
FITTING:   ID:  3658  XCEN:  1550.28  YCEN:  1154.42  MAG:    23.86
FITTING:   ID:  3650  XCEN:  1327.00  YCEN:  1158.02  MAG:    24.29
FITTING:   ID:  3789  XCEN:  1460.00  YCEN:  1184.71  MAG:    25.09
FITTING:   ID:  3849  XCEN:  1355.08  YCEN:  1198.85  MAG:    22.77
FITTING:   ID:  3957  XCEN:  1230.79  YCEN:  1220.03  MAG:    24.84
FITTING:  

FITTING:   ID:  3960  XCEN:  1453.64  YCEN:  1221.90  MAG:    22.90
FITTING:   ID:  4147  XCEN:  1571.99  YCEN:  1272.82  MAG:    23.05
FITTING:   ID:  4224  XCEN:  1236.21  YCEN:  1294.77  MAG:    24.77
FITTING:   ID:  4246  XCEN:  1238.77  YCEN:  1303.95  MAG:    25.33
FITTING:   ID:  4255  XCEN:  1241.27  YCEN:  1308.27  MAG:    25.51
FITTING:   ID:  4642  XCEN:  2491.68  YCEN:  1468.96  MAG:    23.90
FITTING:   ID:  4740  XCEN:  1269.91  YCEN:  1507.13  MAG:    25.29
FITTING:   ID:  4748  XCEN:  1417.66  YCEN:  1515.15  MAG:    24.43
FITTING:   ID:  4799  XCEN:  1339.72  YCEN:  1534.31  MAG:    25.35
FITTING:   ID:  5043  XCEN:  1571.09  YCEN:  1811.40  MAG:    23.52
FITTING:   ID:  5192  XCEN:  1479.52  YCEN:  2030.85  MAG:    23.29
NITER = 14
FITTING:   ID:   127  XCEN:  2494.47  YCEN:   192.82  MAG:    25.13
FITTING:   ID:   233  XCEN:  1000.81  YCEN:   364.74  MAG:    25.48
FITTING:   ID:   406  XCEN:  1539.98  YCEN:   538.28  MAG:    24.03
FITTING:   ID:   484  XCEN:  1536.29 

FITTING:   ID:  2168  XCEN:  1865.36  YCEN:   930.17  MAG:    26.24
FITTING:   ID:  2263  XCEN:  1964.02  YCEN:   946.26  MAG:    23.20
FITTING:   ID:  2286  XCEN:   518.93  YCEN:   955.26  MAG:    21.69
FITTING:   ID:  2350  XCEN:  1595.75  YCEN:   959.11  MAG:    23.49
FITTING:   ID:  2446  XCEN:  1779.85  YCEN:   972.73  MAG:    25.08
FITTING:   ID:  2435  XCEN:  1709.17  YCEN:   972.77  MAG:    24.23
FITTING:   ID:  2593  XCEN:  1337.31  YCEN:  1001.03  MAG:    22.83
FITTING:   ID:  2697  XCEN:  1396.61  YCEN:  1014.88  MAG:    24.33
FITTING:   ID:  2748  XCEN:  1394.55  YCEN:  1017.80  MAG:    23.98
FITTING:   ID:  2981  XCEN:  1477.40  YCEN:  1054.06  MAG:    23.47
FITTING:   ID:  2995  XCEN:  1473.34  YCEN:  1055.42  MAG:    23.91
FITTING:   ID:  3175  XCEN:  1475.97  YCEN:  1081.76  MAG:    24.45
FITTING:   ID:  3415  XCEN:  2241.79  YCEN:  1118.50  MAG:    23.35
FITTING:   ID:  3813  XCEN:  1585.16  YCEN:  1192.65  MAG:    24.82
FITTING:   ID:  4040  XCEN:  1219.90  YCEN:  124

FITTING:   ID:  2868  XCEN:  1519.85  YCEN:  1030.58  MAG:    24.64
FITTING:   ID:  2998  XCEN:  1817.02  YCEN:  1056.91  MAG:    25.73
FITTING:   ID:  3121  XCEN:  1432.63  YCEN:  1069.43  MAG:    23.89
FITTING:   ID:  3357  XCEN:  1830.91  YCEN:  1111.57  MAG:    24.64
FITTING:   ID:  3440  XCEN:  2013.75  YCEN:  1127.16  MAG:    24.99
FITTING:   ID:  3761  XCEN:  1180.11  YCEN:  1182.17  MAG:    22.08
FITTING:   ID:  4268  XCEN:  1455.62  YCEN:  1317.25  MAG:    22.92
FITTING:   ID:  4496  XCEN:   852.55  YCEN:  1414.04  MAG:    24.29
FITTING:   ID:  4627  XCEN:  1380.79  YCEN:  1457.49  MAG:    25.94
NITER = 22
FITTING:   ID:    48  XCEN:  2485.04  YCEN:    77.48  MAG:    24.19
FITTING:   ID:   264  XCEN:  1298.85  YCEN:   418.20  MAG:    26.18
FITTING:   ID:   427  XCEN:  2004.00  YCEN:   542.95  MAG:    22.23
FITTING:   ID:  1175  XCEN:  1917.99  YCEN:   764.65  MAG:    25.28
FITTING:   ID:  2481  XCEN:  1702.95  YCEN:   981.68  MAG:    25.19
FITTING:   ID:  2495  XCEN:  1559.32 

FITTING:   ID:  1058  XCEN:  2064.86  YCEN:   746.82  MAG:    23.84
FITTING:   ID:  1087  XCEN:  2060.92  YCEN:   750.29  MAG:    23.36
FITTING:   ID:  1756  XCEN:  2240.15  YCEN:   871.29  MAG:    25.67
FITTING:   ID:  2355  XCEN:   510.13  YCEN:   960.96  MAG:    21.78
FITTING:   ID:  3780  XCEN:  1236.41  YCEN:  1188.14  MAG:    23.94
NITER = 38
FITTING:   ID:  2978  XCEN:   918.44  YCEN:  1051.98  MAG:    23.92
FITTING:   ID:  4103  XCEN:  1333.85  YCEN:  1270.29  MAG:    23.74
FITTING:   ID:  4450  XCEN:  1036.49  YCEN:  1389.05  MAG:    22.88
FITTING:   ID:  4434  XCEN:  1033.11  YCEN:  1389.67  MAG:    22.50
NITER = 39
FITTING:   ID:  1042  XCEN:  2095.71  YCEN:   748.90  MAG:    24.95
FITTING:   ID:  3594  XCEN:  1892.08  YCEN:  1146.58  MAG:    24.91
FITTING:   ID:  4146  XCEN:  1324.76  YCEN:  1266.92  MAG:    23.66
NITER = 40
FITTING:   ID:    54  XCEN:  2201.95  YCEN:    87.78  MAG:    22.29
FITTING:   ID:   537  XCEN:  2403.51  YCEN:   601.94  MAG:    21.56
FITTING:   ID: 

# 4. Finding Stars Again (if you want)

In [70]:
# 2nd photometry for the subtracted image
# This process is for adding more stars than the previous results by re-running DAOFIND, PHOT, and ALLSTAR tasks.
start_time = time.time()
for i in np.arange(n_img):
    imgname = imglist[i].split(".fits")[0]
    subimage = imgname+".sub.A.fits"
    coofile = imgname+".coo.sub1"
    os.system("rm -rfv "+coofile)
    
    kwargs = {"fwhmpsf":fwhms[i], "sigma":sky_sigma[i], "threshold":3.0, "verify":False}
    iraf.daofind(image=subimage, output=coofile, **kwargs)

    coofile = "HolmIX/HolmIX_g.coo.sub1"
    magfile = imgname+".mag.sub1"
    os.system("rm -rfv "+magfile)
    
    kwargs = {"fwhmpsf":fwhms[i], "sigma":sky_sigma[i],
              "datamax":100.0, "readnoise":5.0, "epadu":3.0, "itime":1.0,
              "cbox":1.5*fwhms[i], "annulus":4*fwhms[i], "dannulus":2*fwhms[i],
              "skyvalue":sky_value[i], "apertures":1.0*fwhms[i], "zmag":27.0, "verify":False}
    iraf.phot(image=subimage, coords=coofile, output=magfile, **kwargs)

    psffile = sorted(glob.glob(imgname+".psf.*.fits"))[-1]
    als0file = imgname+".als.A"    # Previous PSF photometric results
    alsfile = imgname+".als.sub1"    # PSF photometric results from the subtracted image
    rejfile = imgname+".arj.sub1"
    subimage2 = imgname+".sub.sub1.fits"
    os.system("rm -rfv "+alsfile+" "+rejfile+" "+subimage2)

    kwargs = {"fwhmpsf":fwhms[i], "sigma":sky_sigma[i],
              "datamax":100.0, "readnoi":5.0, "epadu":3.0, "itime":1.0,
              "psfrad":4.0*fwhms[i], "fitrad":1.0*fwhms[i]}    
    iraf.allstar(image=subimage, photfile=magfile, psfimage=psffile,
                 allstarfile=alsfile, rejfile=rejfile, subimage=subimage2, **kwargs)
    
    alsnewfile = imgname+".als.new1"    # Merged file of *.als.A and *.als.sub1
    os.system("ls -1 "+als0file+" > merge.lis")
    os.system("ls -1 "+alsfile+" >> merge.lis")
    iraf.pfmerge("@merge.lis", alsnewfile)
    iraf.prenumber(alsnewfile)
    os.system("rm -rfv "+alsfile)
    
    alsfinal = imgname+".als.B"    # The final PSF photometry file
    rejfinal = imgname+".arj.B"
    subfinal = imgname+".sub.B.fits"
    iraf.allstar(image=imglist[i], photfile=alsnewfile, psfimage=psffile,
                 allstarfile=alsfinal, rejfile=rejfinal, subimage=subfinal, **kwargs)
    os.system("rm -rfv "+alsfile+" "+alsnewfile)
    iraf.txdump(alsfinal, "ID,XCENTER,YCENTER,MAG,MSKY", "yes", Stdout=alsfinal+".dat")

    ds9_command = "ds9 -scalemode zscale -scale lock yes -frame lock image "+ \
                  imglist[i]+" "+subfinal+" &"
    os.system(ds9_command)
    
end_time = time.time()
print("\n--- re-DAOFIND, PHOT, ALLSTAR tasks take {0:.4f} sec ---".format(end_time-start_time))


Image: HolmIX/HolmIX_g.sub.A.fits  fwhmpsf: 3.845  ratio: 1.  theta: 0.  nsigma: 1.5

  600.22     1.90   -0.052   0.638   0.944   0.028     1
  372.06     3.47   -0.016   0.586  -0.421   0.315     2
 1670.43     4.80   -0.212   0.364   0.305  -0.096     3
  643.78     5.35   -0.194   0.548  -0.141  -0.109     4
 1893.73     4.44   -0.057   0.447   0.951   0.462     5
  446.78     6.11   -0.296   0.509  -0.271   0.302     6
  577.95     6.22   -0.274   0.310  -0.313   0.149     7
   10.58     6.76   -0.276   0.480   0.362  -0.475     8
  958.97     7.11   -0.316   0.583  -0.044  -0.271     9
 1736.73     6.81   -0.131   0.387  -0.145   0.398    10
  516.00     7.23   -0.016   0.705  -0.421   0.270    11
 2155.68     7.58   -0.014   0.621   0.320  -0.094    12
  582.71     8.45   -0.081   0.362  -0.112   0.689    13
  600.35    10.45   -0.305   0.454  -0.275   0.244    14
   93.48    12.61   -0.213   0.518  -0.132   0.245    15
 1902.04    12.10   -0.030   0.247   0.800  -0.215    16
 

 2055.33   111.09   -0.015   0.564   0.422   0.233   144
 1400.76   111.89   -0.187   0.683   0.294  -0.046   145
 1554.89   112.04   -0.096   0.404   0.035  -0.380   146
 2464.10   111.23   -0.044   0.677   0.784   0.396   147
 2097.78   113.71   -0.018   0.740   0.581  -0.656   148
  341.65   120.41   -0.230   0.625   0.290  -0.068   149
  709.77   120.04   -0.070   0.627   0.191  -0.484   150
  796.14   119.74   -0.004   0.535  -0.175   0.174   151
 1530.97   119.70   -0.035   0.276   0.046  -0.792   152
   54.34   121.08   -0.121   0.574   0.205   0.163   153
  598.46   121.41   -0.396   0.831   0.596  -0.338   154
 2369.36   120.70   -0.046   0.669  -0.424  -0.454   155
 1955.00   124.87   -0.090   0.505  -0.123  -0.747   156
 2315.57   124.98   -0.183   0.208  -0.095  -0.205   157
 1072.31   127.26   -0.008   0.443   0.231   0.832   158
 1683.89   128.05   -0.282   0.323   0.160  -0.173   159
  675.23   128.24   -0.101   0.350  -0.202   0.489   160
  307.52   129.89   -0.223   0.

 2363.88   253.13   -0.002   0.535   0.754   0.087   288
  219.13   253.59   -0.022   0.368   0.367   0.264   289
  604.38   255.71   -0.188   0.522   0.543  -0.037   290
  469.86   255.55   -0.065   0.362   0.563  -0.084   291
  732.13   256.00   -1.169   0.451  -0.326   0.647   292
 1737.73   255.63   -0.040   0.790  -0.442  -0.118   293
 1267.37   256.81   -0.047   0.452   0.107  -0.381   294
  960.38   258.61   -0.148   0.489   0.301   0.244   295
 1633.24   257.60   -0.004   0.423  -0.163  -0.615   296
 1781.75   258.92   -0.191   0.237   0.970  -0.309   297
  378.97   258.64   -0.166   0.471   0.267  -0.138   298
  606.01   259.15   -0.251   0.643   0.511   0.291   299
  739.03   259.50   -0.944   0.474  -0.819   0.993   300
 1236.85   260.43   -0.067   0.642  -0.255  -0.079   301
 1432.31   260.12   -0.081   0.656   0.526   0.326   302
 2298.94   260.79   -0.036   0.455   0.961   0.855   303
  449.79   262.39   -0.157   0.596   0.437   0.610   304
  515.84   264.09   -0.166   0.

  685.98   373.72   -0.195   0.478  -0.167  -0.318   432
 1316.85   373.75   -0.116   0.531   0.857  -0.275   433
 2411.87   374.49   -0.045   0.521  -0.056   0.038   434
 1445.02   376.30   -0.126   0.344  -0.458   0.419   435
 2140.41   376.28   -0.024   0.744   0.144   0.119   436
 1072.34   377.28   -0.126   0.596   0.459  -0.164   437
  431.97   379.64   -0.191   0.406   0.305  -0.132   438
 1019.56   378.83   -0.059   0.306   0.168  -0.473   439
 1022.83   379.61   -0.090   0.632   0.108  -0.460   440
 1502.39   378.36   -0.190   0.529   0.290  -0.014   441
 2341.65   379.08   -0.165   0.559   0.215  -0.198   442
 1241.86   382.85   -0.046   0.600  -0.408  -0.412   443
 1985.77   383.43   -0.089   0.358   0.279  -0.714   444
  499.23   382.45   -0.203   0.771  -0.439  -0.266   445
  345.33   385.00   -0.044   0.704   0.037  -0.392   446
  408.61   385.04   -0.009   0.330   0.492   0.041   447
 1501.62   385.80   -0.078   0.529   0.617   0.030   448
  516.20   387.67   -0.062   0.

 1870.03   482.85   -0.033   0.483  -0.016  -0.821   576
 1337.65   485.42   -0.310   0.620  -0.492  -0.222   577
 1677.65   485.13   -0.480   0.356  -0.704  -0.403   578
 1074.39   485.67   -0.046   0.752  -0.356   0.256   579
 1113.20   486.29   -0.080   0.537   0.230  -0.247   580
  825.64   487.30   -0.120   0.556   0.531   0.202   581
   79.06   487.08   -0.354   0.366   0.814   0.040   582
  803.48   487.90   -0.158   0.598   0.775  -0.146   583
 2134.95   488.03   -0.121   0.489   0.349   0.783   584
 1645.01   489.55   -0.164   0.809   0.080   0.043   585
 1747.06   489.32   -0.003   0.749  -0.552   0.511   586
  152.12   489.95   -0.083   0.489   0.676   0.695   587
  982.68   491.06   -0.144   0.722  -0.991  -0.043   588
 1581.04   491.01   -0.091   0.447   0.325   0.880   589
 1837.56   491.51   -0.082   0.767   0.697   0.220   590
 1539.06   492.48   -0.338   0.287   0.958  -0.536   591
 1768.27   492.25   -0.242   0.467  -0.235  -0.204   592
 2154.56   491.87   -0.267   0.

...

FITTING:   ID:  4476  XCEN:  1844.42  YCEN:   775.71  MAG:    23.12
FITTING:   ID:  8336  XCEN:  1848.11  YCEN:   777.94  MAG:    23.51
REJECTING: Star ID: 5865 is too faint
REJECTING: Star ID: 499 is too faint
FITTING:   ID:  4891  XCEN:   687.40  YCEN:   808.26  MAG:    23.29
FITTING:   ID:  8953  XCEN:   682.51  YCEN:   808.96  MAG:    23.53
REJECTING: Star ID: 7278 is too faint
FITTING:   ID:  6716  XCEN:  1509.39  YCEN:   839.56  MAG:    23.01
REJECTING: Star ID: 3213 is too faint
REJECTING: Star ID: 3221 has merged with star ID: 6729
REJECTING: Star ID: 7308 has merged with star ID: 620
FITTING:   ID:  8352  XCEN:  1366.35  YCEN:   860.22  MAG:    25.33
FITTING:   ID:  3820  XCEN:  1679.39  YCEN:   871.34  MAG:    23.25
FITTING:   ID:  7993  XCEN:  1680.19  YCEN:   873.54  MAG:    24.07
REJECTING: Star ID: 8609 is too faint
FITTING:   ID:   678  XCEN:  1859.57  YCEN:   884.53  MAG:    21.62
FITTING:   ID:  5962  XCEN:  1860.45  YCEN:   885.16  MAG:    23.36
FITTING:   ID:  4654  

FITTING:   ID:  4930  XCEN:  1544.97  YCEN:  1206.24  MAG:    25.38
FITTING:   ID:  6282  XCEN:   926.00  YCEN:  1296.39  MAG:    24.46
FITTING:   ID:  1447  XCEN:   925.90  YCEN:  1297.91  MAG:    22.94
FITTING:   ID:  5129  XCEN:  1430.25  YCEN:  1340.90  MAG:    23.45
FITTING:   ID:  4026  XCEN:   289.73  YCEN:  1467.02  MAG:    23.93
FITTING:   ID:  7044  XCEN:   285.78  YCEN:  1467.32  MAG:    23.23
FITTING:   ID:  4027  XCEN:   282.99  YCEN:  1470.40  MAG:    23.91
FITTING:   ID:  9133  XCEN:  1880.48  YCEN:  2072.03  MAG:    22.64
NITER = 18
FITTING:   ID:  7596  XCEN:  1639.51  YCEN:    25.37  MAG:    23.64
FITTING:   ID:  5090  XCEN:  2218.41  YCEN:    80.86  MAG:    20.68
FITTING:   ID:  5092  XCEN:  2422.76  YCEN:   125.74  MAG:    22.84
FITTING:   ID:  6535  XCEN:   954.68  YCEN:   145.12  MAG:    24.70
FITTING:   ID:  8143  XCEN:   136.11  YCEN:   266.26  MAG:    23.44
FITTING:   ID:  7194  XCEN:   688.47  YCEN:   460.00  MAG:    23.65
FITTING:   ID:  4817  XCEN:   684.14 

FITTING:   ID:  4811  XCEN:  1165.37  YCEN:  1270.65  MAG:    24.70
FITTING:   ID:  9189  XCEN:  1458.95  YCEN:  1313.51  MAG:    24.17
FITTING:   ID:  4948  XCEN:  1457.04  YCEN:  1317.96  MAG:    23.61
FITTING:   ID:  8544  XCEN:  1453.55  YCEN:  1319.81  MAG:    23.36
FITTING:   ID:  1678  XCEN:  1665.01  YCEN:  1527.39  MAG:    22.86
FITTING:   ID:  8654  XCEN:  2185.17  YCEN:  1745.42  MAG:    23.37
FITTING:   ID:  4627  XCEN:  1591.35  YCEN:  1845.35  MAG:    23.36
FITTING:   ID:  4449  XCEN:   247.46  YCEN:  2005.12  MAG:    23.73
FITTING:   ID:  4629  XCEN:   894.80  YCEN:  2077.33  MAG:    23.90
FITTING:   ID:  3707  XCEN:   386.16  YCEN:  2222.27  MAG:    25.00
FITTING:   ID:  7589  XCEN:  1888.82  YCEN:  2228.98  MAG:    23.65
NITER = 22
FITTING:   ID:     6  XCEN:  1063.08  YCEN:    39.68  MAG:    22.32
FITTING:   ID:  8904  XCEN:  1060.38  YCEN:    40.55  MAG:    22.69
FITTING:   ID:  8973  XCEN:  2471.94  YCEN:   776.30  MAG:    22.60
FITTING:   ID:  5116  XCEN:  1563.31 

FITTING:   ID:  8764  XCEN:   944.59  YCEN:  1118.76  MAG:    24.32
FITTING:   ID:  9072  XCEN:  1364.37  YCEN:  1338.04  MAG:    23.29
FITTING:   ID:  7883  XCEN:  1211.87  YCEN:  1490.26  MAG:    24.68
FITTING:   ID:  3631  XCEN:  1208.59  YCEN:  1491.80  MAG:    25.21
FITTING:   ID:  8657  XCEN:   991.40  YCEN:  1868.80  MAG:    24.79
NITER = 32
FITTING:   ID:  5087  XCEN:  2251.98  YCEN:    54.59  MAG:    21.10
FITTING:   ID:  7174  XCEN:   544.48  YCEN:   236.59  MAG:    23.46
FITTING:   ID:  4459  XCEN:  1589.46  YCEN:   358.66  MAG:    25.14
FITTING:   ID:  3786  XCEN:  2472.08  YCEN:   780.23  MAG:    22.52
FITTING:   ID:  5968  XCEN:  1452.79  YCEN:   892.24  MAG:    25.61
REJECTING: Star ID: 9190 has too few good pixels
NITER = 33
FITTING:   ID:  4061  XCEN:  1593.77  YCEN:   360.17  MAG:    24.46
FITTING:   ID:  8727  XCEN:    79.45  YCEN:   487.79  MAG:    22.98
FITTING:   ID:  3090  XCEN:   655.24  YCEN:   621.08  MAG:    23.86
FITTING:   ID:  7872  XCEN:  1366.34  YCEN:  

FITTING:   ID:  4680  XCEN:  1188.10  YCEN:  1185.61  MAG:    23.41
FITTING:   ID:  5053  XCEN:  1326.41  YCEN:  1265.74  MAG:    23.85
FITTING:   ID:  5066  XCEN:  1320.78  YCEN:  1266.08  MAG:    24.28
FITTING:   ID:  7489  XCEN:  1329.34  YCEN:  1269.06  MAG:    23.33
FITTING:   ID:  8775  XCEN:   237.04  YCEN:  1329.16  MAG:    22.79
FITTING:   ID:  5128  XCEN:   227.74  YCEN:  1331.18  MAG:    21.97
FITTING:   ID:  4623  XCEN:  1293.73  YCEN:  1539.34  MAG:    23.30
FITTING:   ID:  9193  XCEN:  1310.08  YCEN:  1543.12  MAG:    17.17
FITTING:   ID:  3660  XCEN:  1972.56  YCEN:  1703.36  MAG:    22.14
FITTING:   ID:  1745  XCEN:  1971.30  YCEN:  1705.45  MAG:    22.69
FITTING:   ID:  9097  XCEN:  1497.63  YCEN:  1807.72  MAG:    22.10
FITTING:   ID:  8982  XCEN:  1492.87  YCEN:  1808.41  MAG:    21.15
FITTING:   ID:  4689  XCEN:  1488.77  YCEN:  1809.96  MAG:    20.75
FITTING:   ID:  4043  XCEN:  1484.38  YCEN:  1810.85  MAG:    21.27
FITTING:   ID:  3669  XCEN:  1725.17  YCEN:  181

In [74]:
if glob.glob(dir_img+"PSF_Phot") == []:
    os.system("mkdir "+dir_img+"PSF_Phot")
for i in np.arange(n_img):
    imgname = imglist[i].split(".fits")[0]
    alsfinal = imgname+".als.B"
    subfinal = imgname+".sub.B.fits"
    psffile = sorted(glob.glob(imgname+".psf.*.fits"))[-1]
    spsffile = sorted(glob.glob(imgname+".spsf.*.fits"))[-1]
    
    os.system("cp -rpv "+alsfinal+" "+subfinal+" "+psffile+" "+spsffile+" "+dir_img+"PSF_Phot/")